##Transformation from Data Cube to df_run (for RCA)
This script contains a prototype transformation workflow from the data cube to the format required by Root Cause Analaysis (RCA) machine learning application. It imports cube directory from the 'configurations' notebook.

###To be completed:
1. Split the results table into two tables to reduce reading overhead for machine learning app
2. Drop columns for signals from stations after the target station
3. Display 'pretty names' (instead of uuid's) of the sensors
4. Implement mechanism to incrementally update the output table as the data streams in

In [0]:
%run "./configurations"

In [0]:
from pyspark.sql.functions import col, concat, concat_ws, lit, collect_list, array_join, desc, first, last, when
import pyspark.sql.functions as f
from pyspark.sql.window import Window

#**********************************************************************************************************************
# HOUSE KEEPING
#**********************************************************************************************************************

# set the number of shuffle partitions to the total number of cores
spark.conf.set("spark.sql.shuffle.partitions", 8)

# load configuration and other variables through Notebook workflow
#dbutils.notebook.run("./configurations", 60)


#**********************************************************************************************************************
# DATA INGESTION: read cube dataframe
#**********************************************************************************************************************

cube_load_df =spark.read.option("mergeSchema", "true").parquet(inputPathDir)


#**********************************************************************************************************************
# DEFINE WINDOWS FOR AGGREGATION
#**********************************************************************************************************************

w1 = (Window.partitionBy("part_number", "serial_number", "run_number")
      .orderBy("timestamp").rowsBetween(Window.unboundedPreceding,Window.unboundedFollowing)
     )
w2 = (Window.partitionBy("part_number", "serial_number", "run_number").orderBy("timestamp")
      .rowsBetween(Window.unboundedPreceding,Window.unboundedFollowing)
     )


#**********************************************************************************************************************
# TRANSFORM STEP: add a column for concatenated path string (path)
#**********************************************************************************************************************

target_join_ops_path_df = (cube_load_df
                           .withColumn("timestamp_first", first("timestamp").over(w1))
                           .withColumn("timestamp_last", last("timestamp").over(w1))
                           .withColumn("path_list", collect_list("station").over(w1))
                           .withColumn("path", array_join("path_list", ','))
                           .drop("path_list")
                          )


#**********************************************************************************************************************
# TRANSFORM STEP: produce 'last' and 'history' measurements columns
#**********************************************************************************************************************
last_history_df = (target_join_ops_path_df
                   .select("part_number", "serial_number", lit(target).alias("target_operation"), "run_number", "pass_fail", 
                           "timestamp_first", "timestamp_last", "path",
                           *[last(c, True).over(w2).alias(c+'_LAST') for c in pivot_feature_cols],
                           *[concat(
                                 lit('{'), 
                                 array_join(
                                     collect_list(
                                         when(col(c).isNotNull(), concat(lit('"'), col("timestamp"), lit('":"'), col(c), lit('"')))
                                         .otherwise(None)
                                      ).over(w2), 
                                   ','
                                 ), 
                                 lit('}')
                             )
                             .alias(c+'_HISTORY')
                             for c in pivot_feature_cols
                            ]
                          )
                   .groupBy("part_number", "serial_number", "target_operation", "run_number", "pass_fail")
                   .agg(first("timestamp_first").alias("timestamp_first"),
                        first("timestamp_last").alias("timestamp_last"),
                        first("path").alias("path"),
                        *[first(c+'_LAST').alias(c+'_LAST') for c in pivot_feature_cols],
                        *[first(c+'_HISTORY').alias(c+'_HISTORY') for c in pivot_feature_cols]
                       )
                   )


#**********************************************************************************************************************
# WRITE DF_RUN TO DISK
# The dataframe is stored in Delta Lake format
#**********************************************************************************************************************
last_history_df.write.format("delta").save(outputDfRunDir)


### for testing, show the generated cube_df
display(last_history_df)

part_number serial_number target_operation run_number pass_fail timestamp_first timestamp_last path 003a5adb-84ac-42cc-8a40-8ab769e37793_data_value_LAST 0135029f-e345-4a01-835a-c9758b114422_data_value_LAST 01c7ae65-eb2f-4c3b-adda-47909f3607e0_data_value_LAST 01ed8563-f7df-48ba-8f9c-931a770256c6_data_value_LAST 0216235c-85b4-4667-85d6-53a9fa0f6497_data_value_LAST 029ef063-639d-43f6-b54f-4d94ab869600_data_value_LAST 03af25ac-7967-41ae-b6ff-917fe9205358_data_value_LAST 04fa520c-4192-4c4b-9a32-1a4e2d49abc9_data_value_LAST 05cdcc75-b1be-4e59-9893-47c7ec54eb6c_data_value_LAST 05ee1df9-6446-4af9-a7a9-d4c86ce158f8_data_value_LAST 06559036-4fd0-45d0-9d58-47c539e52df1_data_value_LAST 07ab9bef-b94b-4416-9334-529830aec9c5_data_value_LAST 0804e486-ea4e-4904-a813-abc8f92c406b_data_value_LAST 080808ff-06f4-4735-baf2-284dc679b258_data_value_LAST 09025ee0-8315-4be6-b39c-22cea2d5160b_data_value_LAST 0ad7a34f-8dcb-4ffb-a004-73527b40ef42_data_value_LAST 0b1cc335-ed4e-419a-84ac-ee58b6d7cc16_data_value_LAST 0b34d0b6-e25a-43b3-9115-2aaff8fe5340_data_value_LAST 0cdc5a0f-fc46-49af-9481-16a990b0edd5_data_value_LAST 0cf2e4fb-f4a1-4209-a36a-47f47854f819_data_value_LAST 0d1fa13b-3561-4aaf-96af-90533a1d78cc_data_value_LAST 101df26c-c76f-4d3a-8c3f-80a1cb8d86ef_data_value_LAST 1038dccf-2c9b-4f24-a90c-7796ec503915_data_value_LAST 13371f7e-71b3-44bd-9f07-3830a1e04111_data_value_LAST 13c80c14-6567-4563-8473-c5184348246d_data_value_LAST 1634fe18-9cca-4c35-9bb5-7a14a919e063_data_value_LAST 173005c3-33c5-453e-9e79-fe6df32f0538_data_value_LAST 1805a47f-00ff-453e-bc40-ab0efcca70ad_data_value_LAST 1988409c-2baa-4966-893e-0d32c8ff15c1_data_value_LAST 1991a9ca-1266-4b26-8cb5-8f19eaa29b16_data_value_LAST 19d443db-2b71-4b4a-a076-d0de8a39f731_data_value_LAST 19f5704f-5462-4b37-a006-28f6242bd5f9_data_value_LAST 1b3bdcfd-12e3-4f08-803a-2e4d205ed8fb_data_value_LAST 1ba8ab6b-8c02-4188-8a8a-190b47f8a3eb_data_value_LAST 1c210ffd-e9ed-4e54-8e12-c08900e56d32_data_value_LAST 1cc4335e-e29c-45f2-9b4b-3b131275385e_data_value_LAST 1d39fcb7-415f-4c0a-b641-5d46cdb7c912_data_value_LAST 1db9643b-f8af-45dd-8a37-684594b977d2_data_value_LAST 1fd465ba-9960-4327-8eb6-b107c36b15f9_data_value_LAST 206ba4a7-52f1-4e8f-809d-9e63be30cac0_data_value_LAST 222973a3-6201-4d6f-a743-8f60b2394b5a_data_value_LAST 222c4e58-c585-4b06-a64c-3e3487afe358_data_value_LAST 237f76f4-68c5-426b-99c5-57d00ac0f7c1_data_value_LAST 24388bc3-5953-4477-9aec-34baba54910c_data_value_LAST 257505e2-b113-4021-92a7-430a9695ba75_data_value_LAST 284cd4cd-9d0a-4055-ba4c-bf29ebe01526_data_value_LAST 2abc23a2-dfa1-4d7a-9355-10bf3bdfcead_data_value_LAST 2b3202d0-e0f1-4a12-b8cc-c60ab5df716e_data_value_LAST 2c329b38-d4da-414a-bc9c-dc61a543bd8b_data_value_LAST 2c85942f-e4a4-415c-bf02-19cc67043356_data_value_LAST 2cd12730-d856-45df-a71c-f76e44e65906_data_value_LAST 2ddce6ed-e684-416c-ac27-62aa0e623939_data_value_LAST 2eb47804-3c56-4c95-b2d6-9b4ff5ea805d_data_value_LAST 2fc7b965-7f82-4a1c-8aea-ca67c991b961_data_value_LAST 31848ef6-70ca-4581-b0ff-3498df7ebd7d_data_value_LAST 32222459-650f-4855-ace1-322e395b5bb1_data_value_LAST 329353ca-90d3-4f9b-819f-8da5e4f85b93_data_value_LAST 33b95cc6-a368-45e9-8fec-2e29917b4cd1_data_value_LAST 3538ccc1-cb81-4001-ad38-37f368137167_data_value_LAST 35481747-9994-4e31-af81-bc3ca4c7320a_data_value_LAST 35823798-dee4-4bef-8215-a49e22146c9c_data_value_LAST 37bb5ee2-0522-4fed-8617-dae672b3a53c_data_value_LAST 3848c376-62a7-4d5a-adb2-04ec8299e9d4_data_value_LAST 38e08747-be0e-45f2-b2e3-aada414dc1b3_data_value_LAST 39cc77c1-e11b-4867-ae60-a16089184bb9_data_value_LAST 3a3c8335-11d4-493d-a172-875ace4fbb67_data_value_LAST 3aa1943c-4e51-49e7-a203-cde4c5e85fd6_data_value_LAST 3b87d8c1-6963-49c0-b100-bcab7a05a8a4_data_value_LAST 3c532eb3-f10e-450a-b71c-ece6add00546_data_value_LAST 3d99d1ef-8344-408e-8461-c36596e97c64_data_value_LAST 3f033066-fde1-46e2-889e-e34b27edf212_data_value_LAST 3fc6baf6-ce78-41cd-92a2-8b8890c25a3b_data_value_LAST 3fc709f6-7ede-4bbd-9628-074e81d203c9_data_value_LAST 419a8623-8796-47e5-a850-fb1b567

In [0]:
### For testing, read back DF_RUN and view data
df_run = spark.read.format('delta').load(outputDfRunDir)
display(df_run)

part_number serial_number target_operation run_number pass_fail timestamp_first timestamp_last path 003a5adb-84ac-42cc-8a40-8ab769e37793_data_value_LAST 0135029f-e345-4a01-835a-c9758b114422_data_value_LAST 01c7ae65-eb2f-4c3b-adda-47909f3607e0_data_value_LAST 01ed8563-f7df-48ba-8f9c-931a770256c6_data_value_LAST 0216235c-85b4-4667-85d6-53a9fa0f6497_data_value_LAST 029ef063-639d-43f6-b54f-4d94ab869600_data_value_LAST 03af25ac-7967-41ae-b6ff-917fe9205358_data_value_LAST 04fa520c-4192-4c4b-9a32-1a4e2d49abc9_data_value_LAST 05cdcc75-b1be-4e59-9893-47c7ec54eb6c_data_value_LAST 05ee1df9-6446-4af9-a7a9-d4c86ce158f8_data_value_LAST 06559036-4fd0-45d0-9d58-47c539e52df1_data_value_LAST 07ab9bef-b94b-4416-9334-529830aec9c5_data_value_LAST 0804e486-ea4e-4904-a813-abc8f92c406b_data_value_LAST 080808ff-06f4-4735-baf2-284dc679b258_data_value_LAST 09025ee0-8315-4be6-b39c-22cea2d5160b_data_value_LAST 0ad7a34f-8dcb-4ffb-a004-73527b40ef42_data_value_LAST 0b1cc335-ed4e-419a-84ac-ee58b6d7cc16_data_value_LAST 0b34d0b6-e25a-43b3-9115-2aaff8fe5340_data_value_LAST 0cdc5a0f-fc46-49af-9481-16a990b0edd5_data_value_LAST 0cf2e4fb-f4a1-4209-a36a-47f47854f819_data_value_LAST 0d1fa13b-3561-4aaf-96af-90533a1d78cc_data_value_LAST 101df26c-c76f-4d3a-8c3f-80a1cb8d86ef_data_value_LAST 1038dccf-2c9b-4f24-a90c-7796ec503915_data_value_LAST 13371f7e-71b3-44bd-9f07-3830a1e04111_data_value_LAST 13c80c14-6567-4563-8473-c5184348246d_data_value_LAST 1634fe18-9cca-4c35-9bb5-7a14a919e063_data_value_LAST 173005c3-33c5-453e-9e79-fe6df32f0538_data_value_LAST 1805a47f-00ff-453e-bc40-ab0efcca70ad_data_value_LAST 1988409c-2baa-4966-893e-0d32c8ff15c1_data_value_LAST 1991a9ca-1266-4b26-8cb5-8f19eaa29b16_data_value_LAST 19d443db-2b71-4b4a-a076-d0de8a39f731_data_value_LAST 19f5704f-5462-4b37-a006-28f6242bd5f9_data_value_LAST 1b3bdcfd-12e3-4f08-803a-2e4d205ed8fb_data_value_LAST 1ba8ab6b-8c02-4188-8a8a-190b47f8a3eb_data_value_LAST 1c210ffd-e9ed-4e54-8e12-c08900e56d32_data_value_LAST 1cc4335e-e29c-45f2-9b4b-3b131275385e_data_value_LAST 1d39fcb7-415f-4c0a-b641-5d46cdb7c912_data_value_LAST 1db9643b-f8af-45dd-8a37-684594b977d2_data_value_LAST 1fd465ba-9960-4327-8eb6-b107c36b15f9_data_value_LAST 206ba4a7-52f1-4e8f-809d-9e63be30cac0_data_value_LAST 222973a3-6201-4d6f-a743-8f60b2394b5a_data_value_LAST 222c4e58-c585-4b06-a64c-3e3487afe358_data_value_LAST 237f76f4-68c5-426b-99c5-57d00ac0f7c1_data_value_LAST 24388bc3-5953-4477-9aec-34baba54910c_data_value_LAST 257505e2-b113-4021-92a7-430a9695ba75_data_value_LAST 284cd4cd-9d0a-4055-ba4c-bf29ebe01526_data_value_LAST 2abc23a2-dfa1-4d7a-9355-10bf3bdfcead_data_value_LAST 2b3202d0-e0f1-4a12-b8cc-c60ab5df716e_data_value_LAST 2c329b38-d4da-414a-bc9c-dc61a543bd8b_data_value_LAST 2c85942f-e4a4-415c-bf02-19cc67043356_data_value_LAST 2cd12730-d856-45df-a71c-f76e44e65906_data_value_LAST 2ddce6ed-e684-416c-ac27-62aa0e623939_data_value_LAST 2eb47804-3c56-4c95-b2d6-9b4ff5ea805d_data_value_LAST 2fc7b965-7f82-4a1c-8aea-ca67c991b961_data_value_LAST 31848ef6-70ca-4581-b0ff-3498df7ebd7d_data_value_LAST 32222459-650f-4855-ace1-322e395b5bb1_data_value_LAST 329353ca-90d3-4f9b-819f-8da5e4f85b93_data_value_LAST 33b95cc6-a368-45e9-8fec-2e29917b4cd1_data_value_LAST 3538ccc1-cb81-4001-ad38-37f368137167_data_value_LAST 35481747-9994-4e31-af81-bc3ca4c7320a_data_value_LAST 35823798-dee4-4bef-8215-a49e22146c9c_data_value_LAST 37bb5ee2-0522-4fed-8617-dae672b3a53c_data_value_LAST 3848c376-62a7-4d5a-adb2-04ec8299e9d4_data_value_LAST 38e08747-be0e-45f2-b2e3-aada414dc1b3_data_value_LAST 39cc77c1-e11b-4867-ae60-a16089184bb9_data_value_LAST 3a3c8335-11d4-493d-a172-875ace4fbb67_data_value_LAST 3aa1943c-4e51-49e7-a203-cde4c5e85fd6_data_value_LAST 3b87d8c1-6963-49c0-b100-bcab7a05a8a4_data_value_LAST 3c532eb3-f10e-450a-b71c-ece6add00546_data_value_LAST 3d99d1ef-8344-408e-8461-c36596e97c64_data_value_LAST 3f033066-fde1-46e2-889e-e34b27edf212_data_value_LAST 3fc6baf6-ce78-41cd-92a2-8b8890c25a3b_data_value_LAST 3fc709f6-7ede-4bbd-9628-074e81d203c9_data_value_LAST 419a8623-8796-47e5-a850-fb1b567